In [35]:
import pandas as pd
import numpy as np

df = pd.read_csv('uber_cleaned.csv')
df.rename(columns = {'pickup_longitude_x': 'pickup_longitude',
                     'pickup_latitude_x': 'pickup_latitude'}, inplace = True)
df.head()

fare_id                            key  fare_amount  \
0  24238194    2015-05-07 19:52:06.0000003          7.5   
1  27835199    2009-07-17 20:04:56.0000002          7.7   
2  44984355   2009-08-24 21:45:00.00000061         12.9   
3  25894730    2009-06-26 08:22:21.0000001          5.3   
4  17610152  2014-08-28 17:47:00.000000188         16.0   

           pickup_datetime  pickup_longitude  pickup_latitude  \
0  2015-05-07 19:52:06 UTC        -73.999817        40.738354   
1  2009-07-17 20:04:56 UTC        -73.994355        40.728225   
2  2009-08-24 21:45:00 UTC        -74.005043        40.740770   
3  2009-06-26 08:22:21 UTC        -73.976124        40.790844   
4  2014-08-28 17:47:00 UTC        -73.925023        40.744085   

   dropoff_longitude  dropoff_latitude  passenger_count  \
0         -73.999512         40.723217                1   
1         -73.994710         40.750325                1   
2         -73.962565         40.772647                1   
3         -73.965316         40.803349                3   
4         -73.973082         40.761247                5   

   pickup_latitude_rounded  ...  haversine_distance  pickup_year  \
0                   40.738  ...            1.683323         2015   
1                   40.728  ...            2.457590         2009   
2                   40.741  ...            5.036377         2009   
3                   40.791  ...            1.661683         2009   
4                   40.744  ...            4.475450         2014   

   pickup_month  pickup_day  pickup_hour  pickup_minute  pickup_dayofweek  \
0             5           7           19             52                 3   
1             7          17           20              4                 4   
2             8          24           21             45                 0   
3             6          26            8             22                 4   
4             8          28           17             47                 3   

   pickup_dayofweek_label fare_per_passenger  sublocality  
0                Thursday           7.500000    Manhattan  
1                  Friday           7.700000    Manhattan  
2                  Monday          12.900000    Manhattan  
3                  Friday           1.766667    Manhattan  
4                Thursday           3.200000       Queens  

[5 rows x 21 columns]

# Questions to answer:
## Business Performance
1. What are the peak demand hours/days?
2. Which locations generate highest revenue per trip?
3. How does fare vary by distance, time, and passenger count?
4. What's the average trip distance and duration proxy?

In [36]:
import plotly.express as px

# Count trips for each hour and day of week
heatmap_data = df.groupby(['pickup_dayofweek_label', 'pickup_hour']).size().reset_index(name='trip_count')

# Pivot for heatmap
heatmap_pivot = heatmap_data.pivot(index='pickup_dayofweek_label', columns='pickup_hour', values='trip_count')

# Plotly heatmap
fig = px.imshow(
    heatmap_pivot,
    labels=dict(x="Pickup Hour", y="Day of Week", color="Trip Count"),
    x=heatmap_pivot.columns,
    y=heatmap_pivot.index,
    aspect="auto",
    title="Uber Trips Heatmap by Hour and Day of Week"
)
fig.show()

In [37]:
# Calculate total and average revenue per pickup location (rounded coordinates for grouping)
pickup_revenue = df.groupby(['sublocality']).agg(
    avg_revenue=('fare_amount', 'mean'),
    trip_count=('fare_amount', 'count')
).reset_index()

pickup_revenue.sort_values('avg_revenue', ascending=False).head(10)

sublocality  avg_revenue  trip_count
3         Queens    29.337320        9661
5  Staten Island    17.382308          13
0       Brooklyn    12.953525        4414
1       Chauncey    12.900000           1
6      The Bronx    12.094585         205
2      Manhattan    10.213950      181151
4         Sobral     8.900000           1

In [38]:
import plotly.graph_objects as go

# Get top 10 locations for visualization
top_locations = pickup_revenue.sort_values('avg_revenue', ascending=False).head(10)

# Bar chart for average revenue
fig = go.Figure(data=[
    go.Bar(x=top_locations['sublocality'], 
           y=top_locations['avg_revenue'],
           marker_color='lightgreen')
])

fig.update_layout(
    title='Average Revenue per Trip by Location',
    xaxis_title='Pickup Location',
    yaxis_title='Average Revenue ($)',
    xaxis_tickangle=45
)

fig.show()

In [39]:
# 3. How does fare vary by distance, time, and passenger count?

import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create distance proxy if not available (using coordinate differences)
if 'trip_distance' not in df.columns:
    df['distance_proxy'] = np.sqrt(
        (df['pickup_longitude'] - df['dropoff_longitude'])**2 + 
        (df['pickup_latitude'] - df['dropoff_latitude'])**2
    ) * 111  # Convert to approximate km

# Create subplots for comprehensive analysis
fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=(
        'Fare vs Distance',
        'Fare by Time of Day', 
        'Fare by Passenger Count',
        'Fare vs Distance by Hour'
    ),
    specs=[[{"secondary_y": False}, {"secondary_y": False}],
           [{"secondary_y": False}, {"secondary_y": False}]]
)

# 1. Fare vs Distance
distance_col = 'trip_distance' if 'trip_distance' in df.columns else 'distance_proxy'
fig.add_trace(
    go.Scatter(
        x=df[distance_col], 
        y=df['fare_amount'],
        mode='markers',
        marker=dict(size=3, opacity=0.6),
        name='Fare vs Distance'
    ),
    row=1, col=1
)

# 2. Fare by Time of Day (hourly average)
hourly_fare = df.groupby('pickup_hour')['fare_amount'].mean().reset_index()
fig.add_trace(
    go.Scatter(
        x=hourly_fare['pickup_hour'],
        y=hourly_fare['fare_amount'],
        mode='lines+markers',
        name='Avg Fare by Hour',
        line=dict(color='orange', width=3)
    ),
    row=1, col=2
)

# 3. Fare by Passenger Count
if 'passenger_count' in df.columns:
    passenger_fare = df.groupby('passenger_count')['fare_amount'].mean().reset_index()
    fig.add_trace(
        go.Bar(
            x=passenger_fare['passenger_count'],
            y=passenger_fare['fare_amount'],
            name='Avg Fare by Passengers',
            marker_color='lightcoral'
        ),
        row=2, col=1
    )

# 4. Distance vs Fare colored by hour (sample for performance)
sample_df = df.sample(n=min(5000, len(df)))  # Sample for performance
fig.add_trace(
    go.Scatter(
        x=sample_df[distance_col],
        y=sample_df['fare_amount'],
        mode='markers',
        marker=dict(
            size=4,
            color=sample_df['pickup_hour'],
            colorscale='Viridis',
            showscale=True,
            colorbar=dict(title="Hour of Day")
        ),
        name='Distance vs Fare by Hour'
    ),
    row=2, col=2
)

# Update layout
fig.update_layout(
    height=800,
    title_text="Fare Analysis: Distance, Time, and Passenger Count",
    showlegend=False
)

# Update axis labels
fig.update_xaxes(title_text="Distance (km)", row=1, col=1)
fig.update_xaxes(title_text="Hour of Day", row=1, col=2)
fig.update_xaxes(title_text="Passenger Count", row=2, col=1)
fig.update_xaxes(title_text="Distance (km)", row=2, col=2)

fig.update_yaxes(title_text="Fare Amount ($)", row=1, col=1)
fig.update_yaxes(title_text="Average Fare ($)", row=1, col=2)
fig.update_yaxes(title_text="Average Fare ($)", row=2, col=1)
fig.update_yaxes(title_text="Fare Amount ($)", row=2, col=2)

fig.show()

# Additional detailed analysis
print("\n=== FARE VARIATION ANALYSIS ===")

# Correlation analysis
print("\n1. CORRELATION WITH DISTANCE:")
distance_corr = df[['fare_amount', distance_col]].corr().iloc[0,1]
print(f"Fare-Distance Correlation: {distance_corr:.3f}")

# Time-based analysis
print("\n2. FARE BY TIME PERIODS:")
df['time_period'] = pd.cut(df['pickup_hour'], 
                          bins=[0, 6, 12, 18, 24], 
                          labels=['Night', 'Morning', 'Afternoon', 'Evening'],
                          include_lowest=True)
time_fare = df.groupby('time_period')['fare_amount'].agg(['mean', 'std', 'count'])
print(time_fare)

# Passenger count analysis (if available)
if 'passenger_count' in df.columns:
    print("\n3. FARE BY PASSENGER COUNT:")
    passenger_analysis = df.groupby('passenger_count').agg({
        'fare_amount': ['mean', 'std', 'count'],
        distance_col: 'mean'
    }).round(2)
    print(passenger_analysis)
    
    # Per-passenger fare
    df['fare_per_passenger'] = df['fare_amount'] / df['passenger_count']
    print("\n4. FARE PER PASSENGER:")
    per_passenger_fare = df.groupby('passenger_count')['fare_per_passenger'].mean()
    print(per_passenger_fare)

# Distance categories analysis
print("\n5. FARE BY DISTANCE CATEGORIES:")
df['distance_category'] = pd.cut(df[distance_col], 
                                bins=[0, 2, 5, 10, float('inf')], 
                                labels=['Short (<2km)', 'Medium (2-5km)', 'Long (5-10km)', 'Very Long (>10km)'])
distance_fare = df.groupby('distance_category')['fare_amount'].agg(['mean', 'median', 'count'])
print(distance_fare)


=== FARE VARIATION ANALYSIS ===

1. CORRELATION WITH DISTANCE:
Fare-Distance Correlation: 0.012

2. FARE BY TIME PERIODS:
                  mean       std  count
time_period                            
Night        11.988305  9.460077  29901
Morning      10.965140  8.846408  53935
Afternoon    11.450096  9.676981  59530
Evening      10.927325  8.281019  56634

3. FARE BY PASSENGER COUNT:
                fare_amount               distance_proxy
                       mean   std   count           mean
passenger_count                                         
1                     11.13  8.93  139134          30.39
2                     11.67  9.52   29428          22.13
3                     11.38  9.14    8881          25.23
4                     11.54  9.35    4276          34.15
5                     11.15  8.94   14009          22.53
6                     12.06  9.55    4272          32.75

4. FARE PER PASSENGER:
passenger_count
1    11.131536
2     5.834242
3     3.794361
4     2.88

/tmp/ipykernel_7246/1213166436.py:119: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.

/tmp/ipykernel_7246/1213166436.py:142: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.



## Pricing Insights
5. Is there dynamic pricing evidence? (fare/km variance by hour)
6. Are there fare anomalies or outliers to investigate?
7. How does passenger count affect per-passenger pricing?

## Operational Patterns
8. What's the geographic distribution of pickups?
9. Are there seasonal trends in ridership/fares?
10. Which trip categories (short/long) dominate?